# XGBoost

In [1]:
from xgboost import XGBClassifier
import optuna
from optuna.samplers import TPESampler
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.metrics import accuracy_score, classification_report
import pandas as pd

d:\anacondamain\envs\test\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
df = pd.read_csv("../data/processed/train_processed.csv")
X = df.drop('outcome', axis=1)
y = df.outcome
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=123)

In [3]:
model = XGBClassifier()
model.fit(X_train, y_train)
y_pred = model.predict(X_test)
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

         0.0       0.70      0.69      0.70       526
         1.0       0.69      0.70      0.69       508

    accuracy                           0.70      1034
   macro avg       0.70      0.70      0.70      1034
weighted avg       0.70      0.70      0.70      1034



# Hyperparameters optimization

In [4]:
def objective(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 50, 1000),
        "max_depth": trial.suggest_int("max_depth", 3, 12),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.3, log=True), 
        "subsample": trial.suggest_float("subsample", 0.5, 1.0), 
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0),
        "gamma": trial.suggest_float("gamma", 0, 5),
        "reg_alpha": trial.suggest_float("reg_alpha", 0, 5),
        "reg_lambda": trial.suggest_float("reg_lambda", 0, 5), 
    }
    
    model = XGBClassifier(**params, random_state=123)
    score = cross_val_score(model, X, y, cv=5, scoring='f1').mean()
    return score

In [5]:
study = optuna.create_study(direction='maximize', sampler=TPESampler(seed=123))
study.optimize(objective, n_trials = 200)
print("Best params ", study.best_params)
print("Best score ", study.best_value)

[I 2025-11-30 16:04:20,687] A new study created in memory with name: no-name-5c9e580c-1244-437a-a164-47bfdf71effe
[I 2025-11-30 16:04:22,891] Trial 0 finished with value: 0.704477408798616 and parameters: {'n_estimators': 712, 'max_depth': 5, 'learning_rate': 0.0006148794955909681, 'subsample': 0.7756573845414456, 'colsample_bytree': 0.8597344848927815, 'gamma': 2.115532300622305, 'reg_alpha': 4.9038209919230775, 'reg_lambda': 3.4241486929243163}. Best is trial 0 with value: 0.704477408798616.
[I 2025-11-30 16:04:24,864] Trial 1 finished with value: 0.7091484219241145 and parameters: {'n_estimators': 507, 'max_depth': 6, 'learning_rate': 0.0015605280310734004, 'subsample': 0.8645248536920208, 'colsample_bytree': 0.7192861223398122, 'gamma': 0.29838948304784174, 'reg_alpha': 1.9902212766521572, 'reg_lambda': 3.6899770286601785}. Best is trial 1 with value: 0.7091484219241145.
[I 2025-11-30 16:04:25,422] Trial 2 finished with value: 0.7084804907607806 and parameters: {'n_estimators': 223

Best params  {'n_estimators': 83, 'max_depth': 11, 'learning_rate': 0.03211207540820109, 'subsample': 0.9901548487834609, 'colsample_bytree': 0.8016140937827169, 'gamma': 2.9350970720590692, 'reg_alpha': 3.111987367755465, 'reg_lambda': 1.5312485784240515}
Best score  0.716392101570057


In [6]:
model = XGBClassifier(**study.best_params, random_state=123)
model.fit(X_train, y_train)
y_pred = model.predict(X_test)
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

         0.0       0.73      0.70      0.72       526
         1.0       0.70      0.74      0.72       508

    accuracy                           0.72      1034
   macro avg       0.72      0.72      0.72      1034
weighted avg       0.72      0.72      0.72      1034



In [7]:
df_test = pd.read_csv("../data/processed/test_processed.csv")
Xtest = df_test.drop('outcome', axis=1)
ytest = df_test.outcome

In [8]:
y_pred = model.predict(Xtest)
print(classification_report(ytest, y_pred))

              precision    recall  f1-score   support

         0.0       0.73      0.71      0.72      1117
         1.0       0.71      0.74      0.72      1096

    accuracy                           0.72      2213
   macro avg       0.72      0.72      0.72      2213
weighted avg       0.72      0.72      0.72      2213



# LightGBM

In [9]:
from lightgbm import LGBMClassifier

In [10]:
def objective(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 50, 1000),
        "max_depth": trial.suggest_int("max_depth", 3, 12),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.3, log=True), 
        "subsample": trial.suggest_float("subsample", 0.5, 1.0), 
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0),
        "gamma": trial.suggest_float("gamma", 0, 5),
        "reg_alpha": trial.suggest_float("reg_alpha", 0, 5),
        "reg_lambda": trial.suggest_float("reg_lambda", 0, 5), 
    }
    
    model = LGBMClassifier(**params, random_state=123)
    score = cross_val_score(model, X, y, cv=5, scoring='f1').mean()
    return score

In [11]:
study_lgbm = optuna.create_study(direction='maximize', sampler=TPESampler(seed=123))
study_lgbm.optimize(objective, n_trials = 200)
print("Best params ", study_lgbm.best_params)
print("Best score ", study_lgbm.best_value)

[I 2025-11-30 16:06:46,587] A new study created in memory with name: no-name-07875ae6-b337-46f9-bdcf-1218ec66fdaa


[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Info] Number of positive: 2060, number of negative: 2072
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000203 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1630
[LightGBM] [Info] Number of data points in the train set: 4132, number of used features: 14
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.498548 -> initscore=-0.005808
[LightGBM] [Info] Start training from score -0.005808
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wit

[I 2025-11-30 16:06:49,509] Trial 0 finished with value: 0.7054027067567895 and parameters: {'n_estimators': 712, 'max_depth': 5, 'learning_rate': 0.0006148794955909681, 'subsample': 0.7756573845414456, 'colsample_bytree': 0.8597344848927815, 'gamma': 2.115532300622305, 'reg_alpha': 4.9038209919230775, 'reg_lambda': 3.4241486929243163}. Best is trial 0 with value: 0.7054027067567895.


[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Info] Number of positive: 2060, number of negative: 2072
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000167 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1630
[LightGBM] [Info] Number of data points in the train set: 4132, number of used features: 14
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.498548 -> initscore=-0.005808
[LightGBM] [Info] Start training from score -0.005808
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -

[I 2025-11-30 16:06:50,691] Trial 1 finished with value: 0.7096375087624305 and parameters: {'n_estimators': 507, 'max_depth': 6, 'learning_rate': 0.0015605280310734004, 'subsample': 0.8645248536920208, 'colsample_bytree': 0.7192861223398122, 'gamma': 0.29838948304784174, 'reg_alpha': 1.9902212766521572, 'reg_lambda': 3.6899770286601785}. Best is trial 1 with value: 0.7096375087624305.


...

[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Info] Number of positive: 2060, number of negative: 2073
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000162 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1638
[LightGBM] [Info] Number of data points in the train set: 4133, number of used features: 14
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.498427 -> initscore=-0.006291
[LightGBM] [Info] Start training from score -0.006291
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Info] Number of positive: 2060, number of negative: 2073
[LightGBM] [Info] Auto-choosing col-wise multi-threading, th

[I 2025-11-30 16:08:31,284] Trial 198 finished with value: 0.7099837002894513 and parameters: {'n_estimators': 113, 'max_depth': 6, 'learning_rate': 0.0069971830399343455, 'subsample': 0.7840948877073355, 'colsample_bytree': 0.8083494260800723, 'gamma': 2.0603765915024765, 'reg_alpha': 4.538906937543781, 'reg_lambda': 3.790819762549036}. Best is trial 66 with value: 0.7147876505147173.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGB

[I 2025-11-30 16:08:31,599] Trial 199 finished with value: 0.7126729418348133 and parameters: {'n_estimators': 93, 'max_depth': 9, 'learning_rate': 0.008398489346290854, 'subsample': 0.7431236209411353, 'colsample_bytree': 0.7775750195747219, 'gamma': 2.2315497530148787, 'reg_alpha': 4.701321591515183, 'reg_lambda': 3.450990330362669}. Best is trial 66 with value: 0.7147876505147173.


[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Info] Number of positive: 2060, number of negative: 2073
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000160 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1638
[LightGBM] [Info] Number of data points in the train set: 4133, number of used features: 14
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.498427 -> initscore=-0.006291
[LightGBM] [Info] Start training from score -0.006291
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Unknown parameter: ga

In [12]:
model_lgbm = LGBMClassifier(**study_lgbm.best_params, random_state=123)
model_lgbm.fit(X_train, y_train)
y_pred = model_lgbm.predict(X_test)
print(classification_report(y_test, y_pred))

[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Warning] Unknown parameter: gamma
[LightGBM] [Info] Number of positive: 2067, number of negative: 2065
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000182 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1620
[LightGBM] [Info] Number of data points in the train set: 4132, number of used features: 14
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500242 -> initscore=0.000968
[LightGBM] [Info] Start training from score 0.000968
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Unknown parameter: gamma
              precision    recall  f1-score   support

         0.0       0.74      0.70      0.72       526
         1.0       0.71      0.75      0.73       508

    accuracy                           0.73      1034
   ma

In [13]:
y_pred = model_lgbm.predict(Xtest)
print(classification_report(ytest, y_pred))

[LightGBM] [Warning] Unknown parameter: gamma
              precision    recall  f1-score   support

         0.0       0.73      0.70      0.71      1117
         1.0       0.71      0.74      0.72      1096

    accuracy                           0.72      2213
   macro avg       0.72      0.72      0.72      2213
weighted avg       0.72      0.72      0.72      2213

